Gares et stations du réseau ferré d'Île-de-France (par ligne)<br>
https://data.iledefrance-mobilites.fr/explore/dataset/emplacement-des-gares-idf/information/?location=16,48.85089,2.51991&basemap=jawg.streets

Stations de métro (Toulouse)<br>
https://data.toulouse-metropole.fr/explore/dataset/stations-de-metro/map/?location=16,43.60215,1.44379&basemap=jawg.streets

Itinéraires de métro dans OpenStreetMap<br>
https://www.data.gouv.fr/fr/datasets/itineraires-de-metro-dans-openstreetmap/

Itinéraires de tramways dans OpenStreetMap<br>
https://www.data.gouv.fr/fr/datasets/itineraires-de-tramways-dans-openstreetmap/

Using GeoPandas to convert Linestring UTM data to LatLong<br>
https://gis.stackexchange.com/questions/351846/using-geopandas-to-convert-linestring-utm-data-to-latlong

Converting UTM to Lat/Long with a geoJSON file in pyproj<br>
https://gis.stackexchange.com/questions/217012/converting-utm-to-lat-long-with-a-geojson-file-in-pyproj

Converting projected coordinates to lat/lon using Python?<br>
https://gis.stackexchange.com/questions/78838/converting-projected-coordinates-to-lat-lon-using-python

pyproj4 / pyproj<br>
https://github.com/pyproj4/pyproj

Turbo87 / utm<br>
https://github.com/Turbo87/utm

Universal Transverse Mercator coordinate system<br>
https://en.wikipedia.org/wiki/Universal_Transverse_Mercator_coordinate_system#From_UTM_coordinates_(E,_N,_Zone,_Hemi)_to_latitude,_longitude_(%CF%86,_%CE%BB)



In [1]:
import pandas as pd
import numpy as np
pd.set_option('display.max_columns', None)
pd.set_option('display.max_rows', None)
import datetime
import math

import geopandas as gpd
import shapely.wkt
from shapely.geometry import Point, LineString
from shapely.geometry.polygon import Polygon
from branca.element import Template, MacroElement
import branca.colormap as cm
import folium
from folium import plugins

import json
import pyproj


## Data transform

In [ ]:
wgs84 = pyproj.Proj(init = 'epsg:4326')
InputGrid = pyproj.Proj(init = 'epsg:3857')

### subway

In [ ]:
# # read file
# with open('data/transport/metro_lignes.json', 'r') as myfile:
#     data = myfile.read()

# # parse file
# subway_lines_df = json.loads(data)

In [ ]:
# # traverse data in json string
# i = 0
# for feature in subway_lines_df['features']:
#     if feature['geometry']['type'] == 'LineString':
#         # all coordinates
#         coords = feature['geometry']['coordinates']
#         print('----- %d -----' % i)
#         print(coords)
        
#         # coordList is for each individual polygon
#         for coordList in coords:
#             lat_grid, lng_grid = coordList
#             # do transformation
#             coordList[0],coordList[1] = pyproj.transform(InputGrid, wgs84,lat_grid, lng_grid)
#     elif feature['geometry']['type'] == 'MultiLineString':
#         len_coord = len(feature['geometry']['coordinates'])
#         for c in range(len_coord):
#             coords = feature['geometry']['coordinates'][c]
#             for coordList in coords:
#                 lat_grid, lng_grid = coordList
#                 coordList[0],coordList[1] = pyproj.transform(InputGrid, wgs84,lat_grid, lng_grid)
#     i += 1



In [ ]:
# # write reprojected json to new file
# with open('data/transport/metro_lignes_v2.json', 'w') as f:
#     f.write(json.dumps(subway_lines_df))

### tramway

In [ ]:
# # read file
# with open('data/transport/tramway_lignes.json', 'r') as myfile:
#     tramway_data = myfile.read()

# # parse file
# tramway_lines_df = json.loads(tramway_data)


In [ ]:
# # traverse data in json string
# i = 0
# for feature in tramway_lines_df['features']:
#     if feature['geometry']['type'] == 'LineString':
#         # all coordinates
#         coords = feature['geometry']['coordinates']
#         print('----- %d -----' % i)
        
#         # coordList is for each individual polygon
#         for coordList in coords:
#             lat_grid, lng_grid = coordList
#             # do transformation
#             coordList[0],coordList[1] = pyproj.transform(InputGrid, wgs84,lat_grid, lng_grid)
#     elif feature['geometry']['type'] == 'MultiLineString':
#         len_coord = len(feature['geometry']['coordinates'])
#         print('----- %d -----' % i)
        
#         for c in range(len_coord):
#             coords = feature['geometry']['coordinates'][c]
#             for coordList in coords:
#                 lat_grid, lng_grid = coordList
#                 coordList[0],coordList[1] = pyproj.transform(InputGrid, wgs84,lat_grid, lng_grid)
#     i += 1


In [ ]:
# # write reprojected json to new file
# with open('data/transport/tramway_lignes_v2.json', 'w') as f:
#     f.write(json.dumps(tramway_lines_df))

## Importing data

In [2]:
subway_lines_df = gpd.read_file('data/transport/metro_lignes_v2.json')
tramway_lines_df = gpd.read_file('data/transport/tramway_lignes_v2.json')

transport_lines_df = subway_lines_df.append(tramway_lines_df)

In [3]:
transport_city_map = {
    'RATP':'Paris',
    'RATP Dev':'Paris',
    'Transkeo':'Paris',
    'Keolis Lille Métropole':'Lille',
    'Régie des Transports Métropolitains':'Marseille',
    'Régie des Transports Marseillais':'Marseille',
    'Keolis Rennes':'Rennes',
    'Tisséo':'Toulouse',
    'Keolis Métropole Orléans':'Orléans',
    'Keolis Bordeaux':'Bordeaux',
    'Keolis Bordeaux Métropole':'Bordeaux',
    'Transdev':'Avignon',
    'Keolis Caen Mobilités':'Caen',
    'T2C':'Clermont-Ferrand',
    'Transvilles':'Valenciennes',
    'Soléa':'Mulhouse',
    'SETRAM':'Le Mans',
    'Kéolis Besançon Mobilités':'Besançon',
    "Transports de l'agglomération de Montpellier":'Montpellier',
    'Semitag Gières':'Gières',
    'Semitag Eybens':'Eybens',
    'Kéolis Tours':'Tours',
    'RD Angers':'Angers',
    'SEMITAN':'Nantes',
    'Lia':'Le Havre',
    'TCAR':'Rouen',
    'CFTA Rhône':'Rhône',
    'Compagnie des Transports Strasbourgeois':'Strasbourg',
    'CTS':'Strasbourg',
    'Divia':'Dijon'
}

In [4]:
def get_transport_city(operator, transport_city_map=transport_city_map):
    if operator in transport_city_map:
        return transport_city_map[operator]
    else:
        return operator


transport_lines_df['city'] = transport_lines_df['operator'].apply(lambda x: get_transport_city(x))

### Subway and tram for Ile-de-France

In [5]:
idf_transport_geo = pd.read_json('data/transport/idf_ligne-transport.geojson')
idf_station_df = pd.read_csv('data/transport/idf-emplacement-des-gares.csv', sep=';', decimal='.')

In [ ]:
idf_station_df.head(2)

In [6]:
idf_station_df['lat'], idf_station_df['lng'] = zip(*idf_station_df['Geo Point'].apply(lambda x: x.split(',')))
idf_station_df['lat'] = idf_station_df['lat'].astype(float)
idf_station_df['lng'] = idf_station_df['lng'].astype(float)
idf_station_df = idf_station_df[idf_station_df['mode_'].isin(['Metro', 'RER'])]

In [7]:
idf_map = folium.Map(location=[48.868, 2.365], zoom_start=12, tiles='Cartodb dark_matter') # 'cartodbpositron'
for line_segment in idf_transport_geo['features']:
    gjson = folium.features.GeoJson(line_segment['geometry'],
                                    style_function = lambda x: {'color': '#00C4B3', 'weight': 1.5})
    idf_map.add_child(gjson)

for i, v in idf_station_df.iterrows():
    folium.CircleMarker(location=[v['lat'], v['lng']],
                        radius=1.2,
                        color='#00C4B3',
                        fill_color='#00C4B3',
                        fill=True).add_to(idf_map)

idf_map#.save('m.html')

### Toulouse

In [8]:
tls_subw_station_df = pd.read_csv('data/transport/tls-stations-de-metro.csv', sep=';', decimal='.')
tls_tram_station_df = pd.read_csv('data/transport/tls-stations-de-tramway.csv', sep=';', decimal='.')

tls_station_df = tls_subw_station_df.append(tls_tram_station_df)

In [9]:
tls_station_df['lat'], tls_station_df['lng'] = zip(*tls_station_df['Geo Point'].apply(lambda x: x.split(',')))
tls_station_df['lat'] = tls_station_df['lat'].astype(float)
tls_station_df['lng'] = tls_station_df['lng'].astype(float)
tls_station_df = tls_station_df[tls_station_df['ligne'].isin(['A', 'B', 'T1'])]

In [ ]:
tls_station_df.head(2)

In [10]:
tls_map = folium.Map(location=[43.607286, 1.434685], zoom_start=12,
                     tiles='Cartodb dark_matter')
for line_segment in transport_lines_df[transport_lines_df['city']=='Toulouse']['geometry']:
    gjson = folium.features.GeoJson(line_segment,
                                    style_function = lambda x: {'color': '#ffa300', 'weight': 1.5})# (255, 163, 0)
    tls_map.add_child(gjson)

for i, v in tls_station_df.iterrows():    
    folium.CircleMarker(location=[v['lat'], v['lng']],
                        radius=1.2,
                        color='#ffa300',
                        fill_color='#ffa300',
                        fill=True).add_to(tls_map)

tls_map

### Lille

In [11]:
def draw_map(city, lat, lng, color='#04bcc4', zoom_start=12, transport_lines_df=transport_lines_df):
    city_map = folium.Map(location=[lat, lng], zoom_start=zoom_start, tiles='Cartodb dark_matter')

    for line_segment in transport_lines_df[transport_lines_df['city']==city]['geometry']:
        gjson = folium.features.GeoJson(line_segment,
                                        style_function = lambda x: {'color': color, 'weight': 1.5})
        city_map.add_child(gjson)
    
    return city_map

In [12]:
draw_map('Lille', 50.653342, 3.066724)

### Marseille

In [14]:
draw_map('Marseille', 43.299982, 5.395500, '#e6571a', zoom_start=13)

### Rennes

In [16]:
draw_map('Rennes', 48.110982, -1.677468, zoom_start=13)

### Orléans

In [18]:
draw_map('Orléans', 47.880015, 1.905978)

### Bordeaux

In [20]:
draw_map('Bordeaux', 44.844960, -0.571498)

### Avignon

In [22]:
draw_map('Avignon', 43.935786, 4.810257, '#f80000', zoom_start=14)

In [46]:
draw_map('Caen', 49.181869, -0.357943, zoom_start=13)

In [49]:
draw_map('Clermont-Ferrand', 45.787482, 3.114099, '#af151c', zoom_start=13) # (175, 21, 28)

In [54]:
draw_map('Valenciennes', 50.389760, 3.520005, '#d63d2b') # (214, 61, 43)

In [57]:
draw_map('Mulhouse', 47.753896, 7.330002, '#f6bf01', zoom_start=13) # (246, 191, 1)

In [69]:
draw_map('Tours', 47.394767, 0.693830)

In [76]:
draw_map('Angers', 47.476569, -0.552175, '#1451a2', zoom_start=13) # (20, 81, 162)

In [24]:
transport_lines_df.city.unique()

array(['Paris', 'Lille', 'Aéroports de Paris', 'Marseille', 'Rennes',
       None, 'Keolis', 'Toulouse', 'BVB', 'BLT', 'TPG', 'Orléans', 'SNCF',
       'Bordeaux', 'Avignon', 'Transilien', 'Caen', 'Clermont-Ferrand',
       'Valenciennes', 'Mulhouse', 'Amitram', 'Saarbahn GmbH', 'Le Mans',
       'Besançon', 'Montpellier', 'Gières', 'Semitag', 'Eybens', 'Tours',
       'Angers', 'Nantes', 'Le Havre', 'Rouen', 'Rhône', 'SNCF:Soléa',
       'TDS', 'Strasbourg', 'Veolia Transport', 'Véolia', 'Dijon',
       'NStCM'], dtype=object)

In [77]:
transport_lines_df[transport_lines_df['city'] == 'Le Mans']

id   osm_id route  type  \
104  france_tram_ltr_routes_line.4205039  4205039  tram  None   
105  france_tram_ltr_routes_line.4205038  4205038  tram  None   
197  france_tram_ltr_routes_line.1838956  1838956  tram  None   
198  france_tram_ltr_routes_line.1838955  1838955  tram  None   

                                                  name short_name ref  \
104  T2 : Bellevue - Hauts de Coulaines => Espal - ...        NaN  T2   
105  T2 : Espal - Arche de la Nature => Bellevue - ...        NaN  T2   
197               T1 : Antarès - MMArena => Université        NaN  T1   
198               T1 : Université => Antarès - MMArena        NaN  T1   

    ref-FR-RATP operator network                             to  \
104         NaN   SETRAM  SETRAM     Espal - Arche de la Nature   
105         NaN   SETRAM  SETRAM  Bellevue - Hauts de Coulaines   
197         NaN   SETRAM  SETRAM                     Université   
198         NaN   SETRAM  SETRAM              Antarès - MMArena   

                              from description opening_hours wheelchair  \
104  Bellevue - Hauts de Coulaines        None          None        yes   
105     Espal - Arche de la Nature        None          None       None   
197              Anatrès - MMArena        None          None        yes   
198                     Université        None          None        yes   

      colour by_night public_transport-version wikidata wikipedia twitter  \
104     None     None                        1     None      None     NaN   
105     blue     None                        1     None      None     NaN   
197  #EB001B      yes                        1     None      None     NaN   
198  #EB001B      yes                        1     None      None     NaN   

    source  note osm_version              osm_timestamp  \
104   None  None          39  2019-04-03T19:26:46+00:00   
105   None  None          41  2019-04-03T19:26:27+00:00   
197   None  None          63  2020-11-06T17:43:51+00:00   
198   None  None          67  2020-11-06T17:43:51+00:00   

                                              geometry   via  \
104  LINESTRING (0.21170 48.02019, 0.21208 48.02007...  None   
105  LINESTRING (0.23390 47.99467, 0.23414 47.99445...  None   
197  LINESTRING (0.22222 47.95601, 0.22291 47.95588...  None   
198  LINESTRING (0.15199 48.01698, 0.15231 48.01694...  None   

                    website   url     city  
104  https://www.setram.fr/  None  Le Mans  
105  https://www.setram.fr/  None  Le Mans  
197  https://www.setram.fr/  None  Le Mans  
198  https://www.setram.fr/  None  Le Mans

In [83]:
draw_map('Le Mans', 47.987969, 0.203589, '#ab1987', zoom_start=13) # (171, 25, 135)